In [30]:
import pystac_client
from odc import stac as odc_stac
from dask.distributed import wait
from dask.distributed import Client, wait
import xarray as xr
import pyproj
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import numpy as np
import rioxarray
import hvplot.xarray
import hvplot.pandas
from rasterio.enums import Resampling
import geopandas as gpd
from rasterio import features
from shapely.geometry import shape
from shapely.geometry import Polygon, MultiPolygon,LinearRing
from shapely.ops import unary_union
import geoviews as gv
from scipy import ndimage

In [2]:
# set up dask client for paralelized computation
client = Client(processes=False, threads_per_worker=2, n_workers=3, memory_limit="12GB")

# Connect to STAC catalog
eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1/")

d:\Programme\video\TU\1Master\5Semester\Projekt\RemoteSensing\RemoteSensing-InterdisciplinaryProject\dynamic-flood-visualization\venv\Lib\site-packages\distributed\node.py:187: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 56455 instead
  warnings.warn(


In [3]:
# we define the time range of the event and coordinates of the area with the bounding_box
time_range = "2018-02-28/2018-02-28"
minlon, maxlon = 22.0, 22.8  
minlat, maxlat = 39.45, 39.75

bounding_box = [minlon, minlat, maxlon, maxlat]

# inside the EODC catalogue we get the GFM collection (Global Flood Monitoring) https://services.eodc.eu/browser/#/v1/collections/GFM?.language=en
search = eodc_catalog.search(collections="GFM", bbox=bounding_box, datetime=time_range)
items_GFM = search.item_collection()

crs = pyproj.CRS.from_wkt(items_GFM[0].properties["proj:wkt2"])

# Set the resolution of the data
resolution = items_GFM[0].properties['gsd']

GFM_dc= odc_stac.load(
    items_GFM, 
    bbox=bounding_box,   # Define the bounding box for the area of interest
    crs=crs,   # Set the coordinate reference system
    #bands=["tuw_likelihood","tuw_flood_extent"],   # Specify the bands to load, comment to load all bands
    resolution=resolution,   # Set the resolution of the data
    dtype='uint8',   # Define the data type
    chunks={"x": 1000, "y": 1000, "time": -1},  # Set the chunk size for Dask
)

GFM_dc = GFM_dc.persist()
wait(GFM_dc)

DoneAndNotDoneFutures(done={<Future: finished, type: numpy.ndarray, key: ('ensemble_likelihood-05f5cee9c8e3c417df4ee6afaaeed843', 0, 1, 2)>, <Future: finished, type: numpy.ndarray, key: ('ensemble_water_extent-05f5cee9c8e3c417df4ee6afaaeed843', 0, 1, 2)>, <Future: finished, type: numpy.ndarray, key: ('ensemble_water_extent-05f5cee9c8e3c417df4ee6afaaeed843', 0, 0, 1)>, <Future: finished, type: numpy.ndarray, key: ('tuw_flood_extent-05f5cee9c8e3c417df4ee6afaaeed843', 0, 1, 3)>, <Future: finished, type: numpy.ndarray, key: ('tuw_likelihood-05f5cee9c8e3c417df4ee6afaaeed843', 0, 0, 1)>, <Future: finished, type: numpy.ndarray, key: ('ensemble_likelihood-05f5cee9c8e3c417df4ee6afaaeed843', 0, 0, 2)>, <Future: finished, type: numpy.ndarray, key: ('dlr_flood_extent-05f5cee9c8e3c417df4ee6afaaeed843', 0, 0, 1)>, <Future: finished, type: numpy.ndarray, key: ('advisory_flags-05f5cee9c8e3c417df4ee6afaaeed843', 0, 0, 0)>, <Future: finished, type: numpy.ndarray, key: ('list_likelihood-05f5cee9c8e3c417d

In [5]:
# Pre-processing
# Substitute 255 for NaNs
GFM_dc["tuw_flood_extent"] = GFM_dc.tuw_flood_extent.where(GFM_dc.tuw_flood_extent!=255).compute()
GFM_dc["tuw_likelihood"] = GFM_dc.tuw_likelihood.where(GFM_dc.tuw_likelihood!=255).compute()
GFM_dc["reference_water_mask"] = GFM_dc.reference_water_mask.where(GFM_dc.reference_water_mask!=255).compute()
GFM_dc["exclusion_mask"] = GFM_dc.exclusion_mask.where(GFM_dc.exclusion_mask!=255).compute()

# Access the variables
tuw_likelihood = GFM_dc["tuw_likelihood"]
tuw_flood_extent = GFM_dc["tuw_flood_extent"]

tuw_likelihood = tuw_likelihood.isel(time=1)
tuw_flood_extent = tuw_flood_extent.isel(time=1)
reference_water_mask = GFM_dc["reference_water_mask"].isel(time=1)
exclusion_mask = GFM_dc["exclusion_mask"].isel(time=1)

#### recalculate the coordinates for base map

In [16]:
# Define bounding box and CRS
target_crs = "EPSG:4326"
minlon, maxlon = 22.0, 22.8
minlat, maxlat = 39.45, 39.75

def reproject_and_clip(da, target_crs, bbox):
    """Reproject and clip a DataArray consistently."""
    # Ensure CRS is written correctly
    if da.rio.crs is None:
        da = da.rio.write_crs(da.rio.crs or da.attrs.get('crs'))
    # Reproject to WGS84
    da_ll = da.rio.reproject(target_crs)
    # Clip to bounding box
    da_clipped = da_ll.rio.clip_box(**bbox)
    return da_clipped

In [17]:
bbox = dict(minx=minlon, maxx=maxlon, miny=minlat, maxy=maxlat)

# Apply the same process to all
da_flood = reproject_and_clip(tuw_flood_extent, target_crs, bbox)
da_likelihood = reproject_and_clip(tuw_likelihood, target_crs, bbox)
da_reference = reproject_and_clip(reference_water_mask, target_crs, bbox)

# Example of creating your binary mask from the aligned flood extent
da_visible = da_flood.where(da_flood == 1)

In [18]:
da_visible.hvplot.image(
    x="x", y="y",
    geo=True,
    tiles="OSM",
    cmap=["darkred"],
    alpha=0.75,
    frame_height=450,
    title="Flood Extent on Map",
    colorbar=False
)

:Overlay
   .WMTS.I  :WMTS   [Longitude,Latitude]
   .Image.I :Image   [x,y]   (tuw_flood_extent)

#### filling holes and smoothing

In [9]:
## fills all holes in the polygon map
def remove_all_holes(geom):
    if geom.geom_type == "Polygon":
        return Polygon(geom.exterior)  # rebuild without interiors
    elif geom.geom_type == "MultiPolygon":
        return type(geom)([Polygon(p.exterior) for p in geom.geoms])
    else:
        return geom


In [10]:
# Create binary mask for flood extent
mask = (da_visible > 0)

#Convert raster to vector polygons
shapes_gen = features.shapes(
    mask.astype(np.uint8).values,
    mask=~np.isnan(da_visible.values),
    transform=da_visible.rio.transform()
)

#Extract only polygons where mask == 1
polygons = [shape(geom) for geom, val in shapes_gen if val == 1]

#Build GeoDataFrame
gdf = gpd.GeoDataFrame(geometry=polygons, crs=da_visible.rio.crs)

## fill all holes 
gdf["geometry"] = gdf["geometry"].apply(remove_all_holes)


#Fix invalid geometries and optionally smooth slightly
gdf["geometry"] = gdf.buffer(0)  # repair topology issues
gdf = gdf.explode(ignore_index=True)

#small smooth — tune distance to your CRS
gdf["geometry"] = gdf.buffer(0.0001).buffer(-0.0001)

C:\Users\jakob\AppData\Local\Temp\ipykernel_9100\2465932364.py:26: UserWarning: Geometry is in a geographic CRS. Results from 'buffer' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf["geometry"] = gdf.buffer(0.0001).buffer(-0.0001)


In [11]:
#plotting
gdf.hvplot.polygons(
    geo=True,
    tiles="OSM",
    color="darkred",
    alpha=0.6,
    frame_height=450,
    title="Flood extent (polygon-smoothed)"
)

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

In [ ]:
## change likelihood to fit the desired plot

#normalize
da_likelihood_norm = (da_likelihood.clip(0, 50)) / 50

# Mask out everything below 0.5
da_likelihood_masked = da_likelihood_norm.where(da_likelihood_norm >= 0.5)

# Define discrete bins
da_likelihood_cats = xr.full_like(da_likelihood_masked, np.nan)

da_likelihood_cats = da_likelihood_cats.where(~((da_likelihood_norm >= 0.5) & (da_likelihood_norm < 0.75)), 1)
da_likelihood_cats = da_likelihood_cats.where(~(da_likelihood_norm >= 0.75), 2)


In [28]:
category_cmap = ["#00BFFF", "#FF1493"] 

# --- Flood polygons ---
poly_plot = gdf.hvplot.polygons(
    geo=True,
    color="darkred",
    alpha=0.4,
    line_color="black",
    legend=False,
    tiles=None
)

likelihood_plot = da_likelihood_cats.hvplot.image(
    x="x", y="y",
    geo=True,
    cmap=category_cmap,
    alpha=0.6,
    colorbar=False,
    tiles=None,
    title="Flood Likelihood Categories"
)

# --- Base map ---
tile_layer = gv.tile_sources.OSM.opts(alpha=0.8)

# --- Combine all ---
overlay = tile_layer * likelihood_plot * poly_plot
overlay.opts(frame_height=450)


:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Image.I    :Image   [x,y]   (tuw_likelihood)
   .Polygons.I :Polygons   [Longitude,Latitude]

In [27]:

###  trying filling for likelihood
mask = da_likelihood_norm > 0.5

filled_mask = ndimage.binary_fill_holes(mask)

da_filled = da_likelihood_norm.where(filled_mask, np.nan)
da_filled = da_filled.where(~filled_mask | mask, 0.5)


da_cat = xr.full_like(da_filled, np.nan)
da_cat = da_cat.where(~((da_filled >= 0.5) & (da_filled < 0.75)), 1)
da_cat = da_cat.where(~(da_filled >= 0.75), 2)

category_cmap = ["#1E90FF", "#FF4500"]  # blue for moderate, orange-red for high

da_cat.hvplot.image(
    x="x", y="y",
    geo=True,
    cmap=category_cmap,
    alpha=0.6,
    colorbar=False,
    tiles="OSM",
    title="TUW Likelihood (holes filled with 0.5)"
)


:Overlay
   .WMTS.I  :WMTS   [Longitude,Latitude]
   .Image.I :Image   [x,y]   (tuw_likelihood)

In [38]:

# --- Strict boolean mask ---
mask = (da_likelihood_norm > 0.5) & np.isfinite(da_likelihood_norm)

# --- Label connected regions (8-connectivity) ---
structure = np.ones((3,3), dtype=int)
labeled, num_features = ndimage.label(mask, structure=structure)

# --- Compute sizes of each labeled region ---
sizes = ndimage.sum(mask, labeled, index=range(1, num_features + 1))

# --- Keep only regions larger than min_size ---
min_size = 2  # single pixels have size=1
keep_labels = np.where(sizes >= min_size)[0] + 1
mask_clean = np.isin(labeled, keep_labels)

# --- Fill holes only inside remaining regions ---
holes_filled = ndimage.binary_fill_holes(mask_clean) & (~mask_clean)

# --- Build final array ---
da_filled = da_likelihood_norm.copy()
# Fill holes with 0.5, keep original values elsewhere
da_filled = da_filled.where(~holes_filled, 0.5)
# Remove isolated pixels
da_filled = da_filled.where(mask_clean, np.nan)


# --- Step 5: Optional — classify into categories ---
da_cat = xr.full_like(da_filled, np.nan)
da_cat = da_cat.where(~((da_filled >= 0.5) & (da_filled < 0.75)), 1)
da_cat = da_cat.where(~(da_filled >= 0.75), 2)

# --- Step 6: Plot ---
category_cmap = ["#4682B4", "#B22222"]  # moderate and high

# --- Flood polygons ---
poly_plot = gdf.hvplot.polygons(
    geo=True,
    color="darkred",
    alpha=0.4,
    line_color="black",
    legend=False,
    tiles=None
)

likelihood_plot = da_cat.hvplot.image(
    x="x", y="y",
    geo=True,
    cmap=category_cmap,
    alpha=0.6,
    colorbar=False,
    tiles=None,
    title="Flood Likelihood Categories"
)

# --- Base map ---
tile_layer = gv.tile_sources.OSM.opts(alpha=0.8)

# --- Combine all ---
overlay = tile_layer * likelihood_plot * poly_plot
overlay.opts(frame_height=450)

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Image.I    :Image   [x,y]   (tuw_likelihood)
   .Polygons.I :Polygons   [Longitude,Latitude]